In [30]:
import json
import time 

from kafka import KafkaProducer

def json_serializer(data):
    return json.dumps(data).encode('utf-8')

server = 'localhost:9092'

producer = KafkaProducer(
    bootstrap_servers=[server],
    value_serializer=json_serializer
)

producer.bootstrap_connected()

True

In [31]:
t0 = time.time()

topic_name = 'test-topic'

for i in range(10):
    message = {'number': i}
    producer.send(topic_name, value=message)
    print(f"Sent: {message}")
    time.sleep(0.05)
    
t1 = time.time()
print(f't1 took {(t1 - t0):.2f} seconds')

producer.flush()
t2 = time.time()
print(f't2 took {(t2 - t1):.2f} seconds')


Sent: {'number': 0}
Sent: {'number': 1}
Sent: {'number': 2}
Sent: {'number': 3}
Sent: {'number': 4}
Sent: {'number': 5}
Sent: {'number': 6}
Sent: {'number': 7}
Sent: {'number': 8}
Sent: {'number': 9}
t1 took 0.62 seconds
t2 took 0.00 seconds


In [32]:
import pandas as pd
df = pd.read_csv('green_tripdata_2019-10.csv')

C:\Users\777\AppData\Local\Temp\ipykernel_9072\3100171351.py:2: DtypeWarning: Columns (3) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('green_tripdata_2019-10.csv')


In [33]:
df.head()

VendorID lpep_pickup_datetime lpep_dropoff_datetime store_and_fwd_flag  \
0       2.0  2019-10-01 00:26:02   2019-10-01 00:39:58                  N   
1       1.0  2019-10-01 00:18:11   2019-10-01 00:22:38                  N   
2       1.0  2019-10-01 00:09:31   2019-10-01 00:24:47                  N   
3       1.0  2019-10-01 00:37:40   2019-10-01 00:41:49                  N   
4       2.0  2019-10-01 00:08:13   2019-10-01 00:17:56                  N   

   RatecodeID  PULocationID  DOLocationID  passenger_count  trip_distance  \
0         1.0           112           196              1.0           5.88   
1         1.0            43           263              1.0           0.80   
2         1.0           255           228              2.0           7.50   
3         1.0           181           181              1.0           0.90   
4         1.0            97           188              1.0           2.52   

   fare_amount  extra  mta_tax  tip_amount  tolls_amount  ehail_fee  \
0         18.0   0.50      0.5        0.00           0.0        NaN   
1          5.0   3.25      0.5        0.00           0.0        NaN   
2         21.5   0.50      0.5        0.00           0.0        NaN   
3          5.5   0.50      0.5        0.00           0.0        NaN   
4         10.0   0.50      0.5        2.26           0.0        NaN   

   improvement_surcharge  total_amount  payment_type  trip_type  \
0                    0.3         19.30           2.0        1.0   
1                    0.3          9.05           2.0        1.0   
2                    0.3         22.80           2.0        1.0   
3                    0.3          6.80           2.0        1.0   
4                    0.3         13.56           1.0        1.0   

   congestion_surcharge  
0                   0.0  
1                   0.0  
2                   0.0  
3                   0.0  
4                   0.0

In [34]:
df_green = df[['lpep_pickup_datetime','lpep_dropoff_datetime','PULocationID','DOLocationID','passenger_count','trip_distance','tip_amount']]

In [35]:
df_green.head()

lpep_pickup_datetime lpep_dropoff_datetime  PULocationID  DOLocationID  \
0  2019-10-01 00:26:02   2019-10-01 00:39:58           112           196   
1  2019-10-01 00:18:11   2019-10-01 00:22:38            43           263   
2  2019-10-01 00:09:31   2019-10-01 00:24:47           255           228   
3  2019-10-01 00:37:40   2019-10-01 00:41:49           181           181   
4  2019-10-01 00:08:13   2019-10-01 00:17:56            97           188   

   passenger_count  trip_distance  tip_amount  
0              1.0           5.88        0.00  
1              1.0           0.80        0.00  
2              2.0           7.50        0.00  
3              1.0           0.90        0.00  
4              1.0           2.52        2.26

In [36]:
for row in df_green.itertuples(index=False):
    row_dict = {col: getattr(row, col) for col in row._fields}
    print(row_dict)
    break

{'lpep_pickup_datetime': '2019-10-01 00:26:02', 'lpep_dropoff_datetime': '2019-10-01 00:39:58', 'PULocationID': 112, 'DOLocationID': 196, 'passenger_count': 1.0, 'trip_distance': 5.88, 'tip_amount': 0.0}


In [37]:
t0 = time.time()

topic_name = 'green-trips'

for row in df_green.itertuples(index=False):
    row_dict = {col: getattr(row, col) for col in row._fields}
    producer.send(topic_name, value=row_dict)
    print(f"Sent: {row_dict}")
    
producer.flush()

t1 = time.time()
print(f'took {(t1 - t0):.2f} seconds')

Sent: {'lpep_pickup_datetime': '2019-10-01 00:26:02', 'lpep_dropoff_datetime': '2019-10-01 00:39:58', 'PULocationID': 112, 'DOLocationID': 196, 'passenger_count': 1.0, 'trip_distance': 5.88, 'tip_amount': 0.0}
Sent: {'lpep_pickup_datetime': '2019-10-01 00:18:11', 'lpep_dropoff_datetime': '2019-10-01 00:22:38', 'PULocationID': 43, 'DOLocationID': 263, 'passenger_count': 1.0, 'trip_distance': 0.8, 'tip_amount': 0.0}
Sent: {'lpep_pickup_datetime': '2019-10-01 00:09:31', 'lpep_dropoff_datetime': '2019-10-01 00:24:47', 'PULocationID': 255, 'DOLocationID': 228, 'passenger_count': 2.0, 'trip_distance': 7.5, 'tip_amount': 0.0}
Sent: {'lpep_pickup_datetime': '2019-10-01 00:37:40', 'lpep_dropoff_datetime': '2019-10-01 00:41:49', 'PULocationID': 181, 'DOLocationID': 181, 'passenger_count': 1.0, 'trip_distance': 0.9, 'tip_amount': 0.0}
Sent: {'lpep_pickup_datetime': '2019-10-01 00:08:13', 'lpep_dropoff_datetime': '2019-10-01 00:17:56', 'PULocationID': 97, 'DOLocationID': 188, 'passenger_count': 1.

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [39]:
import pyspark
from pyspark.sql import SparkSession

pyspark_version = pyspark.__version__
kafka_jar_package = f"org.apache.spark:spark-sql-kafka-0-10_2.12:{pyspark_version}"

spark = SparkSession \
    .builder \
    .master("local[*]") \
    .appName("GreenTripsConsumer") \
    .config("spark.jars.packages", kafka_jar_package) \
    .getOrCreate()

In [40]:
green_stream = spark \
    .readStream \
    .format("kafka") \
    .option("kafka.bootstrap.servers", "localhost:9092") \
    .option("subscribe", "green-trips") \
    .option("startingOffsets", "earliest") \
    .load()

In [41]:
def peek(mini_batch, batch_id):
    first_row = mini_batch.take(1)

    if first_row:
        print(first_row[0])

query = green_stream.writeStream.foreachBatch(peek).start()

In [42]:
query.stop()

In [43]:
from pyspark.sql import types

schema = types.StructType() \
    .add("lpep_pickup_datetime", types.StringType()) \
    .add("lpep_dropoff_datetime", types.StringType()) \
    .add("PULocationID", types.IntegerType()) \
    .add("DOLocationID", types.IntegerType()) \
    .add("passenger_count", types.DoubleType()) \
    .add("trip_distance", types.DoubleType()) \
    .add("tip_amount", types.DoubleType())

In [44]:
from pyspark.sql import functions as F

green_stream = green_stream \
  .select(F.from_json(F.col("value").cast('STRING'), schema).alias("data")) \
  .select("data.*")

In [48]:
green_stream

DataFrame[lpep_pickup_datetime: string, lpep_dropoff_datetime: string, PULocationID: int, DOLocationID: int, passenger_count: double, trip_distance: double, tip_amount: double, timestamp: timestamp]

In [45]:
query = green_stream.writeStream.foreachBatch(peek).start()

In [49]:
query

In [46]:
query.stop()

In [50]:
green_stream = green_stream \
        .withColumn('timestamp', F.current_timestamp())

In [51]:
from pyspark.sql.functions import col
from pyspark.sql.functions import desc

popular_destinations = green_stream.groupBy(
        F.window(col("timestamp"), "5 minutes"),
        green_stream.DOLocationID
    ).count().sort(desc("count"))

In [52]:
query = popular_destinations \
    .writeStream \
    .outputMode("complete") \
    .format("console") \
    .option("truncate", "false") \
    .start()

In [54]:
popular_destinations

DataFrame[window: struct<start:timestamp,end:timestamp>, DOLocationID: int, count: bigint]